<a href="https://colab.research.google.com/github/Evolved360/Neural-Inc/blob/main/Battery_data_extraction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**FINAL YEAR PROJECT - PREDICTING THE VOLTAGE OF BATTERY ELECTRODE MATERIALS**

In [1]:
# Install pymatgen Library
!pip install pymatgen

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 23.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.9/67.9 kB 5.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 332.3/332.3 kB 21.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 561.4/561.4 kB 29.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.8/117.8 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 809.2/809.2 kB 20.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.4/98.4 kB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 526.7/526.7 kB 17.9 MB/s eta 0:00:00


In [2]:
# Update Materials Project (MP) api
!pip install --upgrade mp-api

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.1/97.1 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.0/119.0 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.3/200.3 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 61.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.0/670.0 kB 51.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.0/60.0 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.5/101.5 kB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.0/92.0 kB 12.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 kB 35.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 142.5/142.5 kB 15.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.4/62.4 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━

In [3]:
# Import relevant Libraries
import pymatgen.core as mg
from pymatgen.ext.matproj import MPRester
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

In [5]:
# Assign api key to a variable
api_key = 'AnMvErGYzCmoCAKng6ZINvt3Hb1xYFln'

In [6]:
# import MPrester api and assign to a the variable 'mpr'
mpr = MPRester(api_key)

In [7]:
#Create a list of all possible data that can be extracted about metal-ion batteries
field = ['battery_type', 'battery_id', 'thermo_type', 'battery_formula', 'working_ion', 'num_steps', 'max_voltage_step',
         'last_updated', 'framework', 'framework_formula', 'elements', 'nelements', 'chemsys', 'formula_anonymous', 'warnings',
         'formula_charge', 'formula_discharge', 'max_delta_volume', 'average_voltage', 'capacity_grav', 'capacity_vol',
         'energy_grav', 'energy_vol', 'fracA_charge', 'fracA_discharge', 'stability_charge', 'stability_discharge',
         'id_charge', 'id_discharge', 'host_structure', 'adj_pairs', 'material_ids', 'entries_composition_summary',
         'electrode_object', 'fields_not_requested']

# Define a function that queries battery data based on a given element
def get_battery_data(element):
  with MPRester(api_key) as mpr:
    docs1 = mpr.insertion_electrodes.search(working_ion = [element], fields = ['battery_id', 'battery_type', 'thermo_type',
                                                                                'battery_formula',
                                                                               'working_ion', 'num_steps', 'max_voltage_step', 'last_updated',
                                                                               'framework', 'framework_formula', 'elements', 'nelements', 'chemsys',
                                                                               'formula_anonymous', 'warnings', 'formula_charge', 'formula_discharge',
                                                                               'max_delta_volume', 'average_voltage', 'capacity_grav', 'capacity_vol',
                                                                               'energy_grav', 'energy_vol', 'fracA_charge', 'fracA_discharge', 'stability_charge',
                                                                               'stability_discharge', 'id_charge', 'id_discharge', 'host_structure', 'adj_pairs',
                                                                               'material_ids', 'entries_composition_summary', 'electrode_object'])
    df1 = pd.DataFrame(docs1, columns = field)
    return df1

    # Define a function to eliminate redundant information in battery data
def clean_data(column):
  adjusted_column = column[1]
  return adjusted_column

#A function that returns additional data for charge and discharged battery ids
def get_add_data(material_id, property):
    with MPRester(api_key) as mpr:
        try:
            material_data = mpr.summary.search(material_ids=material_id)
            if not material_data:
                print(f"No data found for {material_id}")
                return None

            if property == 'density':
                density = material_data[0].density
                return density
            elif property == 'volume':
                volume = material_data[0].volume
                return volume
            elif property == 'band_gap':
                band_gap = material_data[0].band_gap
                return band_gap
            elif property == 'energy_above_hull':
                energy_above_hull = material_data[0].energy_above_hull
                return energy_above_hull
            elif property == 'ordering':
                ordering = material_data[0].ordering
                return ordering
            elif property == 'density_atomic':
                density_atomic = material_data[0].density_atomic
                return density_atomic
            else:
                print("Invalid property. Please choose 'density', 'volume', 'band_gap', 'energy_above_hull', 'ordering', or 'density_atomic' as property.")
                return None
        except Exception as e:
            print(f"An error occurred while fetching data for {material_id}: {e}")
            return None


In [13]:
# Extract battery data of all elements using function
Li_data = get_battery_data('Li')
Ca_data = get_battery_data('Ca')
Na_data = get_battery_data('Na')
K_data = get_battery_data('K')
Mg_data = get_battery_data('Mg')
Zn_data = get_battery_data('Zn')
Al_data = get_battery_data('Al')
Y_data = get_battery_data('Y')
Rb_data = get_battery_data('Rb')
Cs_data= get_battery_data('Cs')

<ipython-input-7-3293db942677>:12: DeprecationWarning: Accessing insertion_electrodes data through MPRester.insertion_electrodes is deprecated. Please use MPRester.materials.insertion_electrodes instead.
  docs1 = mpr.insertion_electrodes.search(working_ion = [element], fields = ['battery_id', 'battery_type', 'thermo_type',


Retrieving InsertionElectrodeDoc documents:   0%|          | 0/33 [00:00<?, ?it/s]

In [14]:
# Clean all retrieved data
Li_data[field] = Li_data[field].applymap(clean_data)
Ca_data[field] = Ca_data[field].applymap(clean_data)
Na_data[field] = Na_data[field].applymap(clean_data)
K_data[field] = K_data[field].applymap(clean_data)
Mg_data[field] = Mg_data[field].applymap(clean_data)
Zn_data[field] = Zn_data[field].applymap(clean_data)
Al_data[field] = Al_data[field].applymap(clean_data)
Y_data[field] = Y_data[field].applymap(clean_data)
Rb_data[field] = Rb_data[field].applymap(clean_data)
Cs_data[field] = Cs_data[field].applymap(clean_data)


In [15]:

Li_data['density_charge'] = Li_data['id_charge'].apply(get_add_data, property='density')
Li_data['density_discharge'] = Li_data['id_discharge'].apply(get_add_data, property='density')
Li_data['volume_charge'] = Li_data['id_charge'].apply(get_add_data, property = 'volume')
Li_data['volume_discharge'] = Li_data['id_discharge'].apply(get_add_data, property = 'volume')
Li_data['band_gap_charge'] = Li_data['id_charge'].apply(get_add_data, property = 'band_gap')
Li_data['band_gap_discharge'] = Li_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Li_data['energy_above_hull_charge'] = Li_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Li_data['energy_above_hull_discharge'] = Li_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Li_data['ordering_charge'] = Li_data['id_charge'].apply(get_add_data, property = 'ordering')
Li_data['ordering_discharge'] = Li_data['id_discharge'].apply(get_add_data, property = 'ordering')
Li_data['density_atomic_charge'] = Li_data['id_charge'].apply(get_add_data, property='density_atomic')
Li_data['density_atomic_discharge'] = Li_data['id_discharge'].apply(get_add_data, property='density_atomic')

Ca_data['density_charge'] = Ca_data['id_charge'].apply(get_add_data, property='density')
Ca_data['density_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property='density')
Ca_data['volume_charge'] = Ca_data['id_charge'].apply(get_add_data, property = 'volume')
Ca_data['volume_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property = 'volume')
Ca_data['band_gap_charge'] = Ca_data['id_charge'].apply(get_add_data, property = 'band_gap')
Ca_data['band_gap_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Ca_data['energy_above_hull_charge'] = Ca_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Ca_data['energy_above_hull_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Ca_data['ordering_charge'] = Ca_data['id_charge'].apply(get_add_data, property = 'ordering')
Ca_data['ordering_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property = 'ordering')
Ca_data['density_atomic_charge'] = Ca_data['id_charge'].apply(get_add_data, property='density_atomic')
Ca_data['density_atomic_discharge'] = Ca_data['id_discharge'].apply(get_add_data, property='density_atomic')

Na_data['density_charge'] = Na_data['id_charge'].apply(get_add_data, property='density')
Na_data['density_discharge'] = Na_data['id_discharge'].apply(get_add_data, property='density')
Na_data['volume_charge'] = Na_data['id_charge'].apply(get_add_data, property = 'volume')
Na_data['volume_discharge'] = Na_data['id_discharge'].apply(get_add_data, property = 'volume')
Na_data['band_gap_charge'] = Na_data['id_charge'].apply(get_add_data, property = 'band_gap')
Na_data['band_gap_discharge'] = Na_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Na_data['energy_above_hull_charge'] = Na_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Na_data['energy_above_hull_discharge'] = Na_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Na_data['ordering_charge'] = Na_data['id_charge'].apply(get_add_data, property = 'ordering')
Na_data['ordering_discharge'] = Na_data['id_discharge'].apply(get_add_data, property = 'ordering')
Na_data['density_atomic_charge'] = Na_data['id_charge'].apply(get_add_data, property='density_atomic')
Na_data['density_atomic_discharge'] = Na_data['id_discharge'].apply(get_add_data, property='density_atomic')

K_data['density_charge'] = K_data['id_charge'].apply(get_add_data, property='density')
K_data['density_discharge'] = K_data['id_discharge'].apply(get_add_data, property='density')
K_data['volume_charge'] = K_data['id_charge'].apply(get_add_data, property = 'volume')
K_data['volume_discharge'] = K_data['id_discharge'].apply(get_add_data, property = 'volume')
K_data['band_gap_charge'] = K_data['id_charge'].apply(get_add_data, property = 'band_gap')
K_data['band_gap_discharge'] = K_data['id_discharge'].apply(get_add_data, property = 'band_gap')
K_data['energy_above_hull_charge'] = K_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
K_data['energy_above_hull_discharge'] = K_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
K_data['ordering_charge'] = K_data['id_charge'].apply(get_add_data, property = 'ordering')
K_data['ordering_discharge'] = K_data['id_discharge'].apply(get_add_data, property = 'ordering')
K_data['density_atomic_charge'] = K_data['id_charge'].apply(get_add_data, property='density_atomic')
K_data['density_atomic_discharge'] = K_data['id_discharge'].apply(get_add_data, property='density_atomic')

Mg_data['density_charge'] = Mg_data['id_charge'].apply(get_add_data, property='density')
Mg_data['density_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property='density')
Mg_data['volume_charge'] = Mg_data['id_charge'].apply(get_add_data, property = 'volume')
Mg_data['volume_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property = 'volume')
Mg_data['band_gap_charge'] = Mg_data['id_charge'].apply(get_add_data, property = 'band_gap')
Mg_data['band_gap_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Mg_data['energy_above_hull_charge'] = Mg_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Mg_data['energy_above_hull_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Mg_data['ordering_charge'] = Mg_data['id_charge'].apply(get_add_data, property = 'ordering')
Mg_data['ordering_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property = 'ordering')
Mg_data['density_atomic_charge'] = Mg_data['id_charge'].apply(get_add_data, property='density_atomic')
Mg_data['density_atomic_discharge'] = Mg_data['id_discharge'].apply(get_add_data, property='density_atomic')

Zn_data['density_charge'] = Zn_data['id_charge'].apply(get_add_data, property='density')
Zn_data['density_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property='density')
Zn_data['volume_charge'] = Zn_data['id_charge'].apply(get_add_data, property = 'volume')
Zn_data['volume_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property = 'volume')
Zn_data['band_gap_charge'] = Zn_data['id_charge'].apply(get_add_data, property = 'band_gap')
Zn_data['band_gap_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Zn_data['energy_above_hull_charge'] = Zn_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Zn_data['energy_above_hull_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Zn_data['ordering_charge'] = Zn_data['id_charge'].apply(get_add_data, property = 'ordering')
Zn_data['ordering_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property = 'ordering')
Zn_data['density_atomic_charge'] = Zn_data['id_charge'].apply(get_add_data, property='density_atomic')
Zn_data['density_atomic_discharge'] = Zn_data['id_discharge'].apply(get_add_data, property='density_atomic')

Al_data['density_charge'] = Al_data['id_charge'].apply(get_add_data, property='density')
Al_data['density_discharge'] = Al_data['id_discharge'].apply(get_add_data, property='density')
Al_data['volume_charge'] = Al_data['id_charge'].apply(get_add_data, property = 'volume')
Al_data['volume_discharge'] = Al_data['id_discharge'].apply(get_add_data, property = 'volume')
Al_data['band_gap_charge'] = Al_data['id_charge'].apply(get_add_data, property = 'band_gap')
Al_data['band_gap_discharge'] = Al_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Al_data['energy_above_hull_charge'] = Al_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Al_data['energy_above_hull_discharge'] = Al_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Al_data['ordering_charge'] = Al_data['id_charge'].apply(get_add_data, property = 'ordering')
Al_data['ordering_discharge'] = Al_data['id_discharge'].apply(get_add_data, property = 'ordering')
Al_data['density_atomic_charge'] = Al_data['id_charge'].apply(get_add_data, property='density_atomic')
Al_data['density_atomic_discharge'] = Al_data['id_discharge'].apply(get_add_data, property='density_atomic')

Y_data['density_charge'] = Y_data['id_charge'].apply(get_add_data, property='density')
Y_data['density_discharge'] = Y_data['id_discharge'].apply(get_add_data, property='density')
Y_data['volume_charge'] = Y_data['id_charge'].apply(get_add_data, property = 'volume')
Y_data['volume_discharge'] = Y_data['id_discharge'].apply(get_add_data, property = 'volume')
Y_data['band_gap_charge'] = Y_data['id_charge'].apply(get_add_data, property = 'band_gap')
Y_data['band_gap_discharge'] = Y_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Y_data['energy_above_hull_charge'] = Y_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Y_data['energy_above_hull_discharge'] = Y_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Y_data['ordering_charge'] = Y_data['id_charge'].apply(get_add_data, property = 'ordering')
Y_data['ordering_discharge'] = Y_data['id_discharge'].apply(get_add_data, property = 'ordering')
Y_data['density_atomic_charge'] = Y_data['id_charge'].apply(get_add_data, property='density_atomic')
Y_data['density_atomic_discharge'] = Y_data['id_discharge'].apply(get_add_data, property='density_atomic')

Rb_data['density_charge'] = Rb_data['id_charge'].apply(get_add_data, property='density')
Rb_data['density_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property='density')
Rb_data['volume_charge'] = Rb_data['id_charge'].apply(get_add_data, property = 'volume')
Rb_data['volume_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property = 'volume')
Rb_data['band_gap_charge'] = Rb_data['id_charge'].apply(get_add_data, property = 'band_gap')
Rb_data['band_gap_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Rb_data['energy_above_hull_charge'] = Rb_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Rb_data['energy_above_hull_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Rb_data['ordering_charge'] = Rb_data['id_charge'].apply(get_add_data, property = 'ordering')
Rb_data['ordering_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property = 'ordering')
Rb_data['density_atomic_charge'] = Rb_data['id_charge'].apply(get_add_data, property='density_atomic')
Rb_data['density_atomic_discharge'] = Rb_data['id_discharge'].apply(get_add_data, property='density_atomic')

Cs_data['density_charge'] = Cs_data['id_charge'].apply(get_add_data, property='density')
Cs_data['density_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property='density')
Cs_data['volume_charge'] = Cs_data['id_charge'].apply(get_add_data, property = 'volume')
Cs_data['volume_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property = 'volume')
Cs_data['band_gap_charge'] = Cs_data['id_charge'].apply(get_add_data, property = 'band_gap')
Cs_data['band_gap_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property = 'band_gap')
Cs_data['energy_above_hull_charge'] = Cs_data['id_charge'].apply(get_add_data, property = 'energy_above_hull')
Cs_data['energy_above_hull_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property = 'energy_above_hull')
Cs_data['ordering_charge'] = Cs_data['id_charge'].apply(get_add_data, property = 'ordering')
Cs_data['ordering_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property = 'ordering')
Cs_data['density_atomic_charge'] = Cs_data['id_charge'].apply(get_add_data, property='density_atomic')
Cs_data['density_atomic_discharge'] = Cs_data['id_discharge'].apply(get_add_data, property='density_atomic')



<ipython-input-7-3293db942677>:33: DeprecationWarning: Accessing summary data through MPRester.summary is deprecated. Please use MPRester.materials.summary instead.
  material_data = mpr.summary.search(material_ids=material_id)


Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

...

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

Retrieving SummaryDoc documents:   0%|          | 0/1 [00:00<?, ?it/s]

In [16]:

Li_data.to_csv('Li_data.csv', index=False)
Ca_data.to_csv('Ca_data.csv', index=False)
Na_data.to_csv('Na_data.csv', index=False)
K_data.to_csv('K_data.csv', index=False)
Mg_data.to_csv('Mg_data.csv', index=False)
Zn_data.to_csv('Zn_data.csv', index=False)
Al_data.to_csv('Al_data.csv', index=False)
Y_data.to_csv('Y_data.csv', index=False)
Rb_data.to_csv('Rb_data.csv', index=False)
Cs_data.to_csv('Cs_data.csv', index=False)

In [ ]:
battery_data = pd.concat([Li_data, Ca_data, Na_data, K_data, Mg_data])
battery_data.reset_index(drop=True, inplace=True)

In [ ]:
# Displaying modified battery data
battery_data.info()

In [ ]:
# Remove all irrelevant columns
battery_data.drop(['warnings','fields_not_requested','entries_composition_summary', 'electrode_object','last_updated', 'thermo_type','adj_pairs','battery_type', 'host_structure','material_ids'], axis = 1, inplace = True)

In [ ]:
# Displaying newly modified battery data
battery_data.head()

In [ ]:
plt.figure(figsize=(10, 6))
ax = sns.countplot(battery_data['working_ion'], palette='viridis')

# Get the unique categories and their counts
categories = battery_data['working_ion'].value_counts().index.tolist()
counts = battery_data['working_ion'].value_counts().tolist()

# Create custom legend
legend_labels = [f'{cat}: {count}' for cat, count in zip(categories, counts)]
ax.legend(handles=ax.patches, labels=legend_labels, title='Counts')

In [ ]:
# battery_data['density_charge'] = battery_data['id_charge'].apply(get_density_data)

In [ ]:
#sns.heatmap(battery_data.isnull(), cbar = False)

In [ ]:
Li_data = pd.read_csv('Li_data.csv')